<a href="https://colab.research.google.com/github/anudeepnrao/NeMo/blob/main/NeMo_voice_gen_app.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Voice Sample Generation application
This notebook shows how to use NVIDIA NeMo (https://github.com/NVIDIA/NeMo) to construct a toy demo which will generate a voice in the audio fragment with a computer generated one.

At its core the demo does:


* Adding punctuation and capitalization to the text
* Generating spectrogram from resulting text
* Generating waveform audio from the spectrogram.

## Installation
NeMo can be installed via simple pip command.

In [ ]:
BRANCH = 'r1.21.0'
!python -m pip install git+https://github.com/NVIDIA/NeMo.git@$BRANCH#egg=nemo_toolkit[all]


DEPRECATION: git+https://github.com/NVIDIA/NeMo.git@r1.21.0#egg=nemo_toolkit[all] contains an egg fragment with a non-PEP 508 name pip 25.0 will enforce this behaviour change. A possible replacement is to use the req @ url syntax, and remove the egg fragment. Discussion can be found at https://github.com/pypa/pip/issues/11617
  Cloning https://github.com/NVIDIA/NeMo.git (to revision r1.21.0) to /tmp/pip-install-emqi5_rx/nemo-toolkit_a8d8ab5ae0f647b79e0332366161c5b8
  Running command git clone --filter=blob:none --quiet https://github.com/NVIDIA/NeMo.git /tmp/pip-install-emqi5_rx/nemo-toolkit_a8d8ab5ae0f647b79e0332366161c5b8
  Running command git checkout -b r1.21.0 --track origin/r1.21.0
  Switched to a new branch 'r1.21.0'
  Branch 'r1.21.0' set up to track remote branch 'r1.21.0' from 'origin'.
  Resolved https://github.com/NVIDIA/NeMo.git to commit c0022aec9c8fedd59458935f0378a775b28d0444
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Prepa

In [ ]:
# Ignore pre-production warnings
import warnings
warnings.filterwarnings('ignore')
import nemo
# Import Speech Recognition collection
import nemo.collections.asr as nemo_asr
# Import Natural Language Processing collection
import nemo.collections.nlp as nemo_nlp
# Import Speech Synthesis collection
import nemo.collections.tts as nemo_tts
# We'll use this to listen to audio
import IPython

## Instantiate pre-trained NeMo models which we'll use
``from_pretrained(...)`` API downloads and initialized model directly from the cloud.

We will load audio_sample and convert it to text with QuartzNet ASR model (an action called transcribe).
To convert text back to audio, we actually need to generate spectrogram with FastPitch first and then convert it to actual audio signal using the HiFiGAN vocoder.

In [ ]:
from nemo.collections.tts.models import Tacotron2Model
# Speech Recognition model - QuartzNet
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="stt_en_quartznet15x5").cuda()

# Punctuation and capitalization model
punctuation = nemo_nlp.models.PunctuationCapitalizationModel.from_pretrained(model_name='punctuation_en_distilbert').cuda()

# Spectrogram generator which takes text as an input and produces spectrogram
spectrogram_generator = nemo_tts.models.FastPitchModel.from_pretrained(model_name="tts_en_fastpitch").cuda()
spectrogram_generator_m = Tacotron2Model.from_pretrained("tts_en_tacotron2").cuda()

# Vocoder model which takes spectrogram and produces actual audio
vocoder = nemo_tts.models.HifiGanModel.from_pretrained(model_name="tts_en_hifigan").cuda()
vocoder_m= nemo_tts.models.HifiGanModel.from_pretrained(model_name="tts_en_hifigan").cuda()

[NeMo I 2023-11-22 16:26:02 cloud:58] Found existing object /root/.cache/torch/NeMo/NeMo_1.21.0/stt_en_quartznet15x5/16661021d16e679bdfd97a2a03944c49/stt_en_quartznet15x5.nemo.
[NeMo I 2023-11-22 16:26:02 cloud:64] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.21.0/stt_en_quartznet15x5/16661021d16e679bdfd97a2a03944c49/stt_en_quartznet15x5.nemo
[NeMo I 2023-11-22 16:26:02 common:913] Instantiating model from pre-trained checkpoint


[NeMo W 2023-11-22 16:26:03 modelPT:161] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: /data2/voices/train_1k.json
    sample_rate: 16000
    labels:
    - ' '
    - a
    - b
    - c
    - d
    - e
    - f
    - g
    - h
    - i
    - j
    - k
    - l
    - m
    - 'n'
    - o
    - p
    - q
    - r
    - s
    - t
    - u
    - v
    - w
    - x
    - 'y'
    - z
    - ''''
    batch_size: 32
    trim_silence: true
    max_duration: 16.7
    shuffle: true
    is_tarred: false
    tarred_audio_filepaths: /asr_set_1.2/train/train_{0..1023}.tar
    num_workers: 20
    
[NeMo W 2023-11-22 16:26:03 modelPT:168] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to setup the validation data loader(s). 
   

[NeMo I 2023-11-22 16:26:03 features:289] PADDING: 16
[NeMo I 2023-11-22 16:26:04 save_restore_connector:249] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.21.0/stt_en_quartznet15x5/16661021d16e679bdfd97a2a03944c49/stt_en_quartznet15x5.nemo.
[NeMo I 2023-11-22 16:26:05 cloud:58] Found existing object /root/.cache/torch/NeMo/NeMo_1.21.0/punctuation_en_distilbert/6bdea9786c4395fbbe02e4143d2e1cee/punctuation_en_distilbert.nemo.
[NeMo I 2023-11-22 16:26:05 cloud:64] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.21.0/punctuation_en_distilbert/6bdea9786c4395fbbe02e4143d2e1cee/punctuation_en_distilbert.nemo
[NeMo I 2023-11-22 16:26:05 common:913] Instantiating model from pre-trained checkpoint
[NeMo I 2023-11-22 16:26:08 tokenizer_utils:130] Getting HuggingFace AutoTokenizer with pretrained_model_name: distilbert-base-uncased, vocab_file: /tmp/tmpqtodet0n/tokenizer.vocab_file, merges_files: None, special_tokens_dict: {}, and use_fast: False


Using eos_token, but it is not set yet.
Using bos_token, but it is not set yet.
[NeMo W 2023-11-22 16:26:08 modelPT:251] You tried to register an artifact under config key=tokenizer.vocab_file but an artifact for it has already been registered.
[NeMo W 2023-11-22 16:26:08 modelPT:161] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    use_audio: false
    audio_file: null
    sample_rate: 16000
    use_bucketing: true
    batch_size: 32
    preload_audios: true
    use_tarred_dataset: false
    label_info_save_dir: null
    text_file: text_train.txt
    labels_file: labels_train.txt
    tokens_in_batch: null
    max_seq_length: 128
    num_samples: -1
    use_cache: true
    cache_dir: null
    get_label_frequences: false
    verbose: true
    n_jobs: 0
    tar_metadata_file: null
    tar_shuffle_n: 1
    shard_strategy: scatter
    shuffle: true

[NeMo I 2023-11-22 16:26:11 save_restore_connector:249] Model PunctuationCapitalizationModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.21.0/punctuation_en_distilbert/6bdea9786c4395fbbe02e4143d2e1cee/punctuation_en_distilbert.nemo.
[NeMo I 2023-11-22 16:26:11 cloud:58] Found existing object /root/.cache/torch/NeMo/NeMo_1.21.0/tts_en_fastpitch_align/b7d086a07b5126c12d5077d9a641a38c/tts_en_fastpitch_align.nemo.
[NeMo I 2023-11-22 16:26:11 cloud:64] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.21.0/tts_en_fastpitch_align/b7d086a07b5126c12d5077d9a641a38c/tts_en_fastpitch_align.nemo
[NeMo I 2023-11-22 16:26:11 common:913] Instantiating model from pre-trained checkpoint


...

[NeMo I 2023-11-22 16:27:50 features:289] PADDING: 0
[NeMo I 2023-11-22 16:27:52 save_restore_connector:249] Model HifiGanModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.21.0/tts_hifigan/e6da322f0f7e7dcf3f1900a9229a7e69/tts_hifigan.nemo.
[NeMo I 2023-11-22 16:27:52 cloud:58] Found existing object /root/.cache/torch/NeMo/NeMo_1.21.0/tts_hifigan/e6da322f0f7e7dcf3f1900a9229a7e69/tts_hifigan.nemo.
[NeMo I 2023-11-22 16:27:52 cloud:64] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.21.0/tts_hifigan/e6da322f0f7e7dcf3f1900a9229a7e69/tts_hifigan.nemo
[NeMo I 2023-11-22 16:27:52 common:913] Instantiating model from pre-trained checkpoint


[NeMo W 2023-11-22 16:27:55 modelPT:161] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    dataset:
      _target_: nemo.collections.tts.data.datalayers.MelAudioDataset
      manifest_filepath: /home/fkreuk/data/train_finetune.txt
      min_duration: 0.75
      n_segments: 8192
    dataloader_params:
      drop_last: false
      shuffle: true
      batch_size: 64
      num_workers: 4
    
[NeMo W 2023-11-22 16:27:55 modelPT:168] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to setup the validation data loader(s). 
    Validation config : 
    dataset:
      _target_: nemo.collections.tts.data.datalayers.MelAudioDataset
      manifest_filepath: /home/fkreuk/data/val_finetune.txt
      min_duration: 3
      n_segments: 66150


[NeMo I 2023-11-22 16:27:55 features:289] PADDING: 0


[NeMo W 2023-11-22 16:27:55 features:266] Using torch_stft is deprecated and has been removed. The values have been forcibly set to False for FilterbankFeatures and AudioToMelSpectrogramPreprocessor. Please set exact_pad to True as needed.


[NeMo I 2023-11-22 16:27:55 features:289] PADDING: 0
[NeMo I 2023-11-22 16:27:56 save_restore_connector:249] Model HifiGanModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.21.0/tts_hifigan/e6da322f0f7e7dcf3f1900a9229a7e69/tts_hifigan.nemo.


## Using the models

In [ ]:
raw_text = ''
text = ''

raw_text = "Anudeep N Rao is an active contributor to the open-source community. He has a profile on GitHub where he shares his projects and contributions. One of his notable works includes a SystemVerilog project for the Experiential Learning Component of DSDV. He is also known for his work on a 64 Bit Complex Multiplier. You can reach out to him at anudeep@anrlabs.co.in or visit his blog which is currently under development. His contributions to the field of programming and open-source are commendable."

# Add capitalization and punctuation
res = punctuation.add_punctuation_capitalization(queries=[raw_text])
text = res[0]
print(f'\nRaw recognized text: {raw_text}. \nText with capitalization and punctuation: {text}')

[NeMo I 2023-11-22 16:28:22 punctuation_capitalization_model:1167] Using batch size 1 for inference
[NeMo I 2023-11-22 16:28:22 punctuation_capitalization_infer_dataset:127] Max length: 64
[NeMo I 2023-11-22 16:28:22 data_preprocessing:404] Some stats of the lengths of the sequences:
[NeMo I 2023-11-22 16:28:22 data_preprocessing:406] Min: 118 |                  Max: 118 |                  Mean: 118.0 |                  Median: 118.0
[NeMo I 2023-11-22 16:28:22 data_preprocessing:412] 75 percentile: 118.00
[NeMo I 2023-11-22 16:28:22 data_preprocessing:413] 99 percentile: 118.00


100%|██████████| 8/8 [00:00<00:00, 70.73batch/s]


Raw recognized text: Anudeep N Rao is an active contributor to the open-source community. He has a profile on GitHub where he shares his projects and contributions. One of his notable works includes a SystemVerilog project for the Experiential Learning Component of DSDV. He is also known for his work on a 64 Bit Complex Multiplier. You can reach out to him at anudeep@anrlabs.co.in or visit his blog which is currently under development. His contributions to the field of programming and open-source are commendable.. 
Text with capitalization and punctuation: Anudeep N Rao is an active contributor to the Open-source community. He has a profile on Github where he shares his projects and contributions. One of his notable works includes a SystemVerilog project for the Experiential Learning Component of Dsdv. He is also known for his work on a 64 Bit Complex Multiplier. You can reach out to him at Anudeep@anrlabs.co.in or visit his blog, which is currently under development. His contribution

In [ ]:
# A helper function which combines TTS models to go directly from
# text to audio
def text_to_audio(text):
  parsed = spectrogram_generator.parse(text)
  spectrogram = spectrogram_generator.generate_spectrogram(tokens=parsed)
  audio = vocoder.convert_spectrogram_to_audio(spec=spectrogram)
  return audio.to('cpu').detach().numpy()
def text_to_audio_m(text):
  parsed = spectrogram_generator_m.parse(text)
  spectrogram_m = spectrogram_generator_m.generate_spectrogram(tokens=parsed)
  audio = vocoder_m.convert_spectrogram_to_audio(spec=spectrogram_m)
  return audio.to('cpu').detach().numpy()

## Results

In [ ]:
# This is what was recognized by the ASR model
print(raw_text)

Anudeep N Rao is an active contributor to the open-source community. He has a profile on GitHub where he shares his projects and contributions. One of his notable works includes a SystemVerilog project for the Experiential Learning Component of DSDV. He is also known for his work on a 64 Bit Complex Multiplier. You can reach out to him at anudeep@anrlabs.co.in or visit his blog which is currently under development. His contributions to the field of programming and open-source are commendable.


In [ ]:
# This is how punctuation model changed it
print(text)

Anudeep N Rao is an active contributor to the Open-source community. He has a profile on Github where he shares his projects and contributions. One of his notable works includes a SystemVerilog project for the Experiential Learning Component of Dsdv. He is also known for his work on a 64 Bit Complex Multiplier. You can reach out to him at Anudeep@anrlabs.co.in or visit his blog, which is currently under development. His contributions to the field of programming and open-source are commendable.


Compare how the synthesized audio sounds when using text with and without punctuation.

In [ ]:
# Without punctuation
IPython.display.Audio(text_to_audio(raw_text), rate=22050)

[NeMo W 2023-11-22 16:31:29 fastpitch:291] parse() is meant to be called in eval mode.
[NeMo W 2023-11-22 16:31:30 fastpitch:368] generate_spectrogram() is meant to be called in eval mode.


In [ ]:
# Final result - with punctuation
IPython.display.Audio(text_to_audio(text), rate=22050)

[NeMo W 2023-11-22 16:32:19 fastpitch:291] parse() is meant to be called in eval mode.
[NeMo W 2023-11-22 16:32:20 fastpitch:368] generate_spectrogram() is meant to be called in eval mode.


In [ ]:
# Final result - with punctuation - Male Voice
IPython.display.Audio(text_to_audio_m(text), rate=22050)

[NeMo W 2023-11-22 16:33:04 tacotron2:144] parse() is meant to be called in eval mode.
[NeMo W 2023-11-22 16:33:07 tacotron2:341] Reached max decoder steps 1000.


## Next steps
A demo like this is great for prototyping and experimentation. However, for real production deployment, you would want to use a service like [NVIDIA Riva](https://developer.nvidia.com/riva).

**NeMo is built for training.** You can fine-tune, or train from scratch on your data all models used in this example. We recommend you checkout the following, more in-depth, tutorials next:

* [NeMo fundamentals](https://colab.research.google.com/github/NVIDIA/NeMo/blob/stable/tutorials/00_NeMo_Primer.ipynb)
* [NeMo models](https://colab.research.google.com/github/NVIDIA/NeMo/blob/stable/tutorials/01_NeMo_Models.ipynb)
* [Speech Recognition](https://colab.research.google.com/github/NVIDIA/NeMo/blob/stable/tutorials/asr/ASR_with_NeMo.ipynb)
* [Punctuation and Capitalization](https://colab.research.google.com/github/NVIDIA/NeMo/blob/stable/tutorials/nlp/Punctuation_and_Capitalization.ipynb)
* [Speech Synthesis](https://colab.research.google.com/github/NVIDIA/NeMo/blob/stable/tutorials/tts/Inference_ModelSelect.ipynb)


You can find scripts for training and fine-tuning ASR, NLP and TTS models [here](https://github.com/NVIDIA/NeMo/tree/main/examples).

That's it folks! Head over to NeMo GitHub for more examples: https://github.com/NVIDIA/NeMo